# Creating a Model with BuildingMOTIF

[BuildingMOTIF](https://github.com/NREL/BuildingMOTIF) is a Python SDK for creating, manipulating, and validating semantic building models.
Here, we will demonstrate how to create a simple ASHRAE 223P model using BuildingMOTIF.

We will create a model that includes a simple HVAC system with a VAV terminal unit serving a zone.
This will use BuildingMOTIF [Templates](https://buildingmotif.readthedocs.io/en/latest/explanations/templates.html), which are reusable components that encapsulate common patterns in building modeling.

## Setting up BuildingMOTIF

<details>
<summary>Downloading the NREL 223P templates library</summary>

In [1]:
!git clone --filter=blob:none --no-checkout https://github.com/NREL/BuildingMOTIF
!pushd BuildingMOTIF && git sparse-checkout init --cone
!pushd BuildingMOTIF && git sparse-checkout set libraries/ashrae/223p/nrel-templates
!pushd BuildingMOTIF && git checkout

Cloning into 'BuildingMOTIF'...


remote: Enumerating objects: 16864, done.
remote: Counting objects: 100% (1708/1708), done.


remote: Compressing objects: 100% (605/605), done.


remote: Total 16864 (delta 1370), reused 1169 (delta 1100), pack-reused 15156 (from 3)
Receiving objects: 100% (16864/16864), 2.03 MiB | 34.68 MiB/s, done.


Resolving deltas: 100% (8942/8942), done.


~/work/docs.open223.info/docs.open223.info/tutorials/BuildingMOTIF ~/work/docs.open223.info/docs.open223.info/tutorials


~/work/docs.open223.info/docs.open223.info/tutorials/BuildingMOTIF ~/work/docs.open223.info/docs.open223.info/tutorials


~/work/docs.open223.info/docs.open223.info/tutorials/BuildingMOTIF ~/work/docs.open223.info/docs.open223.info/tutorials


remote: Enumerating objects: 19, done.
remote: Counting objects: 100% (7/7), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 19 (delta 0), reused 0 (delta 0), pack-reused 12 (from 2)
Receiving objects: 100% (19/19), 116.37 KiB | 10.58 MiB/s, done.
Resolving deltas: 100% (1/1), done.
Your branch is up to date with 'origin/develop'.


</details>

The following code sets up a temporary (in-memory) BuildingMOTIF instance, loads the necessary libraries, and creates an (empty) model to hold our building data.

In [2]:
from rdflib import Namespace
from buildingmotif import BuildingMOTIF
from buildingmotif.dataclasses import Library, Model
from buildingmotif.model_builder import TemplateBuilderContext as ModelBuilder
import logging

# Create a BuildingMOTIF object. If you do not have Java installed, remove the "shacl_engine" parameter
bm = BuildingMOTIF('sqlite://', shacl_engine='topquadrant', log_level=logging.ERROR)

# load 223P library and some dependencies. We will load a recent copy from the open223.info
s223 = Library.load(ontology_graph="https://open223.info/223p.ttl")
unit = Library.load(ontology_graph="http://qudt.org/3.1.1/vocab/unit")
quantitykind = Library.load(ontology_graph="http://qudt.org/3.1.1/vocab/quantitykind")
templates = Library.load(directory="BuildingMOTIF/libraries/ashrae/223p/nrel-templates")

# create a Model to hold our building model
model = Model.create("urn:example")
BLDG = Namespace("urn:example/")

/home/runner/work/docs.open223.info/docs.open223.info/.venv/lib/python3.12/site-packages/pyshacl/extras/__init__.py:46: Warning: Extra "js" is not satisfied because requirement pyduktape2 is not installed.
  warn(Warning(f"Extra \"{extra_name}\" is not satisfied because requirement {req} is not installed."))


## Building the Model

Now, we load the templates into a `ModelBuilder` context, which allows us to use the templates to create our model.

In [3]:
builder = ModelBuilder(BLDG)
builder.add_templates_from_library(templates)

We will create a reheat VAV terminal unit serving a physical space

In [4]:
# Create a VAV terminal unit with reheat
vav = builder["vav-reheat"](name="my_vav")
# we can give names to the sensors inside the VAV
vav["sup-air-temp-sensor"] = "BLDG_VAV:SAT"
vav["sup-air-flow-sensor"] = "BLDG_VAV:SAF"

# create the physical space
zone = builder["hvac-space"](name="my_zone")

# connect the VAV terminal unit to the zone using a duct
duct2zone = builder["duct"](a=vav['air-out'], b=zone['in'], name="duct2zone")

When we are done, compile the "builder" into the model

In [5]:
model.add_graph(builder.compile())
print(f"Model has {len(model.graph)} triples")

Model has 191 triples


/home/runner/work/docs.open223.info/docs.open223.info/.venv/lib/python3.12/site-packages/buildingmotif/dataclasses/template.py:483: UserWarning: Parameters "rhc-air-out-mapsto, rhc-valve-in, rhc-return-water-temp-sensor, air-in-mapsto, rhc-supply-water-temp, rhc-water-out, sup-air-pressure-sensor, air-out-mapsto, dmp-feedback, rhc-valve-feedback, rhc-air-out, rhc-valve-command, rhc-valve, rhc-valve-out-mapsto, dmp-in, rhc-water-in-mapsto, dmp, dmp-out, sup-air-flow, rhc-air-in, rhc-return-water-temp, rhc-air-in-mapsto, dmp-out-mapsto, sup-air-pressure, rhc-water-in, sup-air-temp, air-in, dmp-in-mapsto, c0, dmp-command, rhc-water-out-mapsto, rhc, rhc-supply-water-temp-sensor, rhc-valve-out, rhc-valve-in-mapsto" were not provided during evaluation
  warnings.warn(
/home/runner/work/docs.open223.info/docs.open223.info/.venv/lib/python3.12/site-packages/buildingmotif/dataclasses/template.py:483: UserWarning: Parameters "exh-flow-sensor, in3, out2-mapsto, in-mapsto, physical-space, in4-maps

The model is now ready and contains the VAV terminal unit and the physical space it serves:

<details>
<summary>223P model generated from templates</summary>

In [6]:
print(model.graph.serialize())

@prefix ns1: <http://data.ashrae.org/standard223#> .
@prefix ns2: <http://qudt.org/schema/qudt/> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .

<urn:example> a owl:Ontology .

<urn:example/c0_48a8784a> a ns1:Duct ;
    rdfs:label "Duct" ;
    ns1:cnx <urn:example/dmp-out_cb1b1e10>,
        <urn:example/rhc-air-in_e4b6530c> ;
    ns1:hasMedium ns1:Fluid-Air .

<urn:example/duct2zone> a ns1:Duct ;
    rdfs:label "Duct" ;
    ns1:cnx <urn:example/air-out_a2d28396>,
        <urn:example/in_6d4ece4b> ;
    ns1:hasMedium ns1:Fluid-Air .

<urn:example/exh-flow-sensor_d52b5412> a ns1:Sensor ;
    rdfs:label "Sensor" ;
    ns1:hasObservationLocation <urn:example/out_56b24c21> ;
    ns1:hasPhysicalLocation <urn:example/physical-space_78f9537b> ;
    ns1:observes <urn:example/exhaust-air-flow_e8b66465> .

<urn:example/humidity-sensor_ce1bc4e6> a ns1:Sensor ;
    rdfs:label "Sensor" ;
    ns1:hasObservationLocation <urn:example/my_zone> ;

</details>

## Compiling the Model

The generated model is the "pre-inference" model, as described in [model_inference.md](model_inference.md).
To apply inference rules to this model, we will need to load the 223P ontology and apply the inference rules as described in that document.

In [7]:
compiled_model = model.compile([s223.get_shape_collection(), unit.get_shape_collection(), quantitykind.get_shape_collection()])
print(f"Compiled model has {len(compiled_model.graph)} triples")

Compiled model has 103646 triples


<details>
<summary>223P model with all inferred triples</summary>

In [8]:
print(compiled_model.graph.serialize())

@prefix dc: <http://purl.org/dc/elements/1.1/> .
@prefix dcterms: <http://purl.org/dc/terms/> .
@prefix ns1: <http://qudt.org/schema/qudt/> .
@prefix ns2: <http://www.linkedmodel.org/schema/vaem#> .
@prefix ns3: <http://data.ashrae.org/standard223#> .
@prefix ns4: <http://sample.org/doc#> .
@prefix owl: <http://www.w3.org/2002/07/owl#> .
@prefix prov: <http://www.w3.org/ns/prov#> .
@prefix rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#> .
@prefix rdfs: <http://www.w3.org/2000/01/rdf-schema#> .
@prefix sh: <http://www.w3.org/ns/shacl#> .
@prefix skos: <http://www.w3.org/2004/02/skos/core#> .
@prefix xsd: <http://www.w3.org/2001/XMLSchema#> .

ns3:AbstractClass a ns3:Class,
        ns3:Concept,
        rdfs:Class,
        sh:NodeShape ;
    rdfs:label "Class"^^xsd:string ;
    rdfs:comment "This is a modeling construct. Instances of abstract classes cannot be created. All abstract classes in this standard have a more specific subclass."^^xsd:string ;
    rdfs:subClassOf ns3:Class .

n

</details>